In [1]:
# Notebook parameters. Values here are for development only and 
# will be overridden when running via snakemake and papermill.
cohort_id = "CD-NU_Gbadolite_gamb_2015_Q3"
# cohort_id = 'ML-2_Kati_colu_2014_Q3'
# cohort_id = 'CI-LG_Agneby-Tiassa_colu_2012'
cohorts_analysis = "20230223"
contigs = ['2RL', '3RL', 'X']
sample_sets = "3.0"
min_cohort_size = 20
max_cohort_size = 50
h12_calibration_contig = '3L'
use_gcs_cache = False
dask_scheduler = "threads"

In [2]:
# Parameters
min_cohort_size = 20
max_cohort_size = 50
sample_sets = ["3.0"]
contigs = ["2RL", "3RL", "X"]
cohorts_analysis = "20230223"
h12_calibration_contig = "3L"
h12_signal_detection_min_delta_aic = 1000
h12_signal_detection_min_stat_max = 0.1
h12_signal_detection_gflanks = [6]
use_gcs_cache = False
dask_scheduler = "single-threaded"
cohort_id = "GN-F_Kissidougou_gamb_2012_Q4"


In [3]:
from IPython.display import Markdown, HTML
import malariagen_data
import numpy as np
import pandas as pd
from pyprojroot import here
import yaml
import dask
dask.config.set(scheduler=dask_scheduler);
from textwrap import dedent

import geopandas as gpd
import bokeh.layouts as bklay
import bokeh.plotting as bkplt
import bokeh.models as bkmod
import plotly.express as px

from bokeh.io import output_notebook # enables plot interface in J notebook

# N.B., do not add the "remove-output" tag to this cell!!! If you do,
# the bokeh javascript libraries will not get loaded in the generated
# HTML page. The call to output_notebook() injects javascript in the
# cell output which triggers the bokeh javascript libraries to be loaded
# in the page.
output_notebook(hide_banner=True)

# Guinea / Kissidougou / gambiae / 2012 / Q4

In [4]:
# Load cohorts to find sample query to select samples for this cohort.

df_cohorts = gpd.read_file(here() / "build" / "final_cohorts.geojson").set_index("cohort_id")
cohort = df_cohorts.loc[cohort_id]
cohort

cohort_size                                                          50
country                                                          Guinea
admin1_iso                                                         GN-F
admin1_name                                                     Faranah
admin2_name                                                 Kissidougou
taxon                                                           gambiae
year                                                               2012
quarter                                                               4
cohort_label                 Guinea / Kissidougou / gambiae / 2012 / Q4
sample_query          cohort_admin2_quarter == 'GN-F_Kissidougou_gam...
latitude                                                           9.28
longitude                                                        -10.03
h12_window_size                                                  1000.0
country_alpha2                                                  

In [5]:
# Initialise access to MalariaGEN data.

extra_params = dict()
if use_gcs_cache:
    extra_params["url"] = "simplecache::gs://vo_agam_release"
    extra_params["simplecache"] = dict(cache_storage=(here() / "gcs_cache").as_posix())

ag3 = malariagen_data.Ag3(
    # Pin the version of the cohorts analysis for reproducibility.
    cohorts_analysis=cohorts_analysis,
    results_cache=(here() / "malariagen_data_cache").as_posix(),
    **extra_params,
)
ag3

<MalariaGEN Ag3 API client>
Storage URL             : gs://vo_agam_release/
Data releases available : 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8
Results cache           : /home/sanjaynagi/selection-atlas/malariagen_data_cache
Cohorts analysis        : 20230223
AIM analysis            : 20220528
Site filters analysis   : dt_20200416
Software version        : malariagen_data 7.13.0
Client location         : unknown
---
Please note that data are subject to terms of use,
for more information see https://www.malariagen.net/data
or contact data@malariagen.net. For API documentation see 
https://malariagen.github.io/vector-data/ag3/api.html

In [6]:
# Load sample metadata for this cohort.

df_samples = ag3.sample_metadata(sample_query=cohort['sample_query'])
df_samples

sample_id partner_sample_id       contributor country location  year  \
0       AV0025-C             KB281       Ken Vernick  Guinea  Koraboh  2012   
1       AV0006-C             KB016       Ken Vernick  Guinea  Koraboh  2012   
2       AV0008-C             KB051       Ken Vernick  Guinea  Koraboh  2012   
3       AV0015-C             KB089       Ken Vernick  Guinea  Koraboh  2012   
4       AV0010-C             KB057       Ken Vernick  Guinea  Koraboh  2012   
5       AV0007-C             KB041       Ken Vernick  Guinea  Koraboh  2012   
6       AV0012-C             KB066       Ken Vernick  Guinea  Koraboh  2012   
7       AV0024-C             KB162       Ken Vernick  Guinea  Koraboh  2012   
8       AV0002-C             KB002       Ken Vernick  Guinea  Koraboh  2012   
9       AV0014-C             KB088       Ken Vernick  Guinea  Koraboh  2012   
10      AV0013-C             KB081       Ken Vernick  Guinea  Koraboh  2012   
11      AV0005-C             KB010       Ken Vernick  Guinea  Koraboh  2012   
12      AV0011-C             KB058       Ken Vernick  Guinea  Koraboh  2012   
13      AV0018-C             KB111       Ken Vernick  Guinea  Koraboh  2012   
14      AV0009-C             KB054       Ken Vernick  Guinea  Koraboh  2012   
15      AV0001-C             KB001       Ken Vernick  Guinea  Koraboh  2012   
16      AV0017-C             KB110       Ken Vernick  Guinea  Koraboh  2012   
17      AV0022-C             KB128       Ken Vernick  Guinea  Koraboh  2012   
18      AV0020-C             KB118       Ken Vernick  Guinea  Koraboh  2012   
19      AV0021-C             KB124       Ken Vernick  Guinea  Koraboh  2012   
20      AV0023-C             KB152       Ken Vernick  Guinea  Koraboh  2012   
21     AV0004-Cx             KB008       Ken Vernick  Guinea  Koraboh  2012   
22     AV0003-Cx             KB003       Ken Vernick  Guinea  Koraboh  2012   
23     AV0069-CW            KV0446       Ken Vernick  Guinea  Koraboh  2012   
24     AV0126-CW            KV0270       Ken Vernick  Guinea  Koraboh  2012   
25      AV0132-C            KV0186       Ken Vernick  Guinea  Koraboh  2012   
26      AV0061-C            KV0189       Ken Vernick  Guinea  Koraboh  2012   
27      AV0109-C            KV0195       Ken Vernick  Guinea  Koraboh  2012   
28      AV0074-C            KV0201       Ken Vernick  Guinea  Koraboh  2012   
29      AV0086-C            KV0202       Ken Vernick  Guinea  Koraboh  2012   
30      AV0098-C            KV0205       Ken Vernick  Guinea  Koraboh  2012   
31      AV0134-C            KV0209       Ken Vernick  Guinea  Koraboh  2012   
32      AV0113-C            KV0244       Ken Vernick  Guinea  Koraboh  2012   
33      AV0137-C            KV0248       Ken Vernick  Guinea  Koraboh  2012   
34      AV0078-C            KV0256       Ken Vernick  Guinea  Koraboh  2012   
35      AV0055-C            KV0275       Ken Vernick  Guinea  Koraboh  2012   
36      AV0067-C            KV0280       Ken Vernick  Guinea  Koraboh  2012   
37      AV0115-C            KV0311       Ken Vernick  Guinea  Koraboh  2012   
38      AV0068-C            KV0325       Ken Vernick  Guinea  Koraboh  2012   
39      AV0080-C            KV0333       Ken Vernick  Guinea  Koraboh  2012   
40      AV0092-C            KV0335       Ken Vernick  Guinea  Koraboh  2012   
41      AV0104-C            KV0340       Ken Vernick  Guinea  Koraboh  2012   
42      AV0116-C            KV0343       Ken Vernick  Guinea  Koraboh  2012   
43      AV0128-C            KV0344       Ken Vernick  Guinea  Koraboh  2012   
44      AV0140-C            KV0347       Ken Vernick  Guinea  Koraboh  2012   
45      AV0094-C            KV0464       Ken Vernick  Guinea  Koraboh  2012   
46      AV0059-C            KV0475       Ken Vernick  Guinea  Koraboh  2012   
47      AV0083-C            KV0477       Ken Vernick  Guinea  Koraboh  2012   
48      AV0095-C            KV0479       Ken Vernick  Guinea  Koraboh  2012   
49      AV0119-C            KV0482       Ken Vernick  Gui

In [7]:
# Determine collection dates.

df_collection_dates = (
    df_samples
    .groupby(["year", "month"])
    .size()
    .reset_index()
    .rename(columns={0: 'count'})
)
df_collection_dates

year  month  count
0  2012     10     51

In [8]:
# Determine first and last collection months.

min_month = df_collection_dates["month"].min()
max_month = df_collection_dates["month"].max()

if min_month < 0:
    start_month = end_month = None
else:
    start_month = pd.to_datetime(min_month, format="%m").month_name()
    end_month = pd.to_datetime(max_month, format="%m").month_name()
    
start_month, end_month

('October', 'October')

In [9]:
# Determine unique collection locations.

df_locations = df_samples[["location", "longitude", "latitude"]].drop_duplicates()
df_locations

location  longitude  latitude
0   Koraboh    -10.030     9.280
50   Korabo     -9.999     9.275

In [10]:
# Extract provenance information about the samples.

df_contributors = df_samples[["release", "sample_set", "contributor"]].drop_duplicates()
df_contributors["study"] = df_contributors.apply(
    lambda v: "Ag1000G" if v["sample_set"].startswith("AG1000G") else "TODO",
    axis="columns"
)
df_contributors["release"] = df_contributors["release"].apply(
    lambda v: f"Ag{v}"
)
df_contributors.rename(columns={
    "contributor": "Contributor",
    "study": "Study",
    "release": "Data release",
    "sample_set": "Sample set",
}, inplace=True)
df_contributors.set_index(["Contributor", "Study", "Data release"], inplace=True)
df_contributors

Sample set
Contributor      Study   Data release               
Ken Vernick      Ag1000G Ag3.0          AG1000G-GN-A
                         Ag3.0          AG1000G-GN-B
Jacob E Crawford TODO    Ag3.7         crawford-2016

In [11]:
# Build a paragraph with summary information about the samples in this cohort.

n_locations = len(df_locations)

summary_info = f"""This cohort comprises {cohort['cohort_size']:,} samples from the 
*{cohort['taxon']}* taxon, collected from {n_locations} locations within the administrative 
division of {cohort['admin2_name']}, {cohort['admin1_name']}, {cohort['country']}."""

if start_month and start_month == end_month:
    summary_info += f""" Collections were made in {start_month} {cohort['year']}."""
elif start_month:
    summary_info += f""" Collections were made between {start_month} and {end_month} in {cohort['year']}."""
else:
    summary_info += f""" Collections were made in {cohort['year']}."""
    
display(Markdown(summary_info))


This cohort comprises 50 samples from the 
*gambiae* taxon, collected from 2 locations within the administrative 
division of Kissidougou, Faranah, Guinea. Collections were made in October 2012.

## Selection scans

In [12]:
# load signals to overlay on H12 plots
import pandas as pd

df_signals_contigs = []
for contig in contigs:

    try:
        df_signals_contig = pd.read_csv(here() / "build/h12-signal-detection/" / f"{cohort_id}_{contig}.csv")
    except pd.errors.EmptyDataError:
        df_signals_contig = pd.DataFrame()
    df_signals_contigs.append(df_signals_contig)  
    
df_signals = pd.concat(df_signals_contigs)

# Add extra columns to help with overlaying signals on plots.
df_signals["bottom"] = 0
df_signals["top"] = 1

df_signals

cohort_id contig     gcenter    pcenter  delta_i  \
0  GN-F_Kissidougou_gamb_2012_Q4    2RL   56.907290   28453646     6786   
1  GN-F_Kissidougou_gamb_2012_Q4    2RL  120.683630   64112446     2928   
2  GN-F_Kissidougou_gamb_2012_Q4    2RL  166.611470   87076367     1130   
3  GN-F_Kissidougou_gamb_2012_Q4    2RL  172.746941   90144102     2251   
4  GN-F_Kissidougou_gamb_2012_Q4    2RL  194.144396  100842830     2270   
0  GN-F_Kissidougou_gamb_2012_Q4    3RL   57.104566   28552283     6178   
0  GN-F_Kissidougou_gamb_2012_Q4      X   30.105527   15052764     3034   

   stat_max    gpos_max   ppos_max  focus_gstart  focus_gstop  ...      skew  \
0    0.1826   56.947866   28473933     56.835030    57.048952  ... -0.485584   
1    0.9802  120.074432   63216998    120.367928   121.084038  ... -0.171456   
2    0.1440  166.455514   86998388    166.493127   166.848158  ... -0.500000   
3    0.1730  172.714212   90127737    172.460569   172.890127  ...  0.500000   
4    0.1060  194.093222  100817242    194.106834   194.163177  ...  0.500000   
0    0.3736   57.119268   28559634     57.005854    57.191301  ...  0.093304   
0    0.2540   30.386922   15193461     29.984514    30.335961  ... -0.464601   

   decay_left  decay_right  baseline           aic           bic        rss  \
0    0.289042     0.566646  0.015918 -21386.735267 -21358.595112   0.061791   
1    1.262807     1.601634  0.036690  -6831.577199  -6804.921898  17.299128   
2    0.473375     0.946749  0.040390 -15792.464172 -15764.558122   0.620543   
3    1.145487     0.572743  0.029612 -14671.690489 -14644.019347   0.731435   
4    0.150247     0.075124  0.016291 -21117.016355 -21089.195163   0.033582   
0    0.394847     0.346940  0.020732 -17071.945674 -17044.304016   0.190995   
0    0.484049     0.921737  0.024376 -15102.409660 -15074.598851   0.746379   

   constant_aic  bottom  top  
0 -14600.347028       0    1  
1  -3902.827823       0    1  
2 -14661.791366       0    1  
3 -12419.967971       0    1  
4 -18846.932466       0    1  
0 -10893.595246       0    1  
0 -12068.407339       0    1  

[7 rows x 32 columns]

In [13]:
# load window sizes 
h12_calibration_dir = "build/h12-calibration"
with open(here() / h12_calibration_dir / f"{cohort_id}.yaml") as h12_calibration_file:
    h12_calibration_params = yaml.safe_load(h12_calibration_file)
h12_window_size = h12_calibration_params["h12_window_size"]
g123_calibration_dir = "build/g123-calibration"
with open(here() / g123_calibration_dir / f"{cohort_id}.yaml") as g123_calibration_file:
    g123_calibration_params = yaml.safe_load(g123_calibration_file)
g123_window_size = g123_calibration_params["g123_window_size"]

if cohort.taxon == 'arabiensis':
    phasing_analysis = 'arab'
else:
    phasing_analysis = 'gamb_colu'

ihs_window_size = 100

def plot_h12_g123_ihs_tracks(
        contig, 
        df_signals,
        sizing_mode='stretch_width', 
        show=False, 
        width=800, 
        track_height=150,
        genes_height=90,
    ):

    sample_query = cohort["sample_query"]
    
    fig1 = ag3.plot_h12_gwss_track(
        contig=contig, 
        window_size=h12_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        show=show,
        width=width,
        height=track_height,
    )
    fig1.xaxis.visible = False
        
    if not df_signals.empty:
        df = df_signals.query("contig == @contig")
        center_xs = [np.array([row.pcenter, row.pcenter]) for idx, row in df.iterrows()]
        center_ys = [np.array([0, 1]) for idx, row in df.iterrows()]
        source = bkmod.ColumnDataSource(data={
            'cohort': df.cohort_id,
            'chromosome': df.contig,
            'score': df.delta_i.astype(int),
            'peak_start': df.span2_pstart,
            'peak_stop': df.span2_pstop,
            'focus_start': df.focus_pstart,
            'focus_stop': df.focus_pstop,    
            'center_xs': center_xs,
            'center_ys': center_ys,
            'bottom': df.bottom ,
            'top': df.top,
            })
        quad = fig1.quad(bottom='bottom', top='top', left='peak_start', right='peak_stop', 
              source=source, color="gray", alpha=.1, line_width=1)
        quad2 = fig1.quad(bottom='bottom', top='top', left='focus_start', right='focus_stop', 
              source=source, color="red", alpha=.4)
        glyph = bkmod.MultiLine(xs='center_xs', ys='center_ys', line_color='red', line_width=2, line_alpha=0.8)
        fig1.add_glyph(source, glyph)
    
        hover = bkmod.HoverTool(tooltips=[
            ("Cohort", '@cohort'),
            ("Score", '@score'),
            ("Focus", "@focus_start{,} - @focus_stop{,}"),
        ], renderers=[quad])

        fig1.add_tools(hover)
    
    fig2 = ag3.plot_g123_gwss_track(
        contig=contig, 
        window_size=g123_window_size, 
        sites=phasing_analysis,
        site_mask=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig2.xaxis.visible = False

    fig3 = ag3.plot_ihs_gwss_track(
        contig=contig, 
        window_size=ihs_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig3.xaxis.visible = False


    fig4 = ag3.plot_genes(
        region=contig, 
        show=show,
        sizing_mode=sizing_mode,
        width=width,
        height=genes_height,
        x_range=fig1.x_range
        )
                        
    fig = bklay.gridplot(
        [fig1, fig2, fig3, fig4],
        ncols=1,
        toolbar_location="above",
        merge_tools=True,
        sizing_mode=sizing_mode,
    )
    return fig 

In [14]:
for contig in contigs:
    
    display(HTML(f"<h3>Chromosome {contig}</h3>"))
    
    fig = plot_h12_g123_ihs_tracks(
        contig=contig,
        df_signals=df_signals,
    );

    bkplt.show(fig)


## Sampling information

In [15]:
from ipyleaflet import Map, Marker, basemaps
from ipywidgets import HTML

center = cohort[['latitude', 'longitude']].to_list()
m = Map(center=center, zoom=9, basemap=basemaps.OpenTopoMap)

df = df_samples[['latitude', 'longitude', 'taxon']].groupby(['latitude', 'longitude', 'taxon']).size().to_frame().rename(columns={0: 'count'}).reset_index()

for coh_id, row in df.iterrows():
    lat, long = row[['latitude', 'longitude']]
    
    if row['taxon'] == 'gambiae':
        color= 'red'
    elif row['taxon'] == 'coluzzii':
        color='cadetblue'
    elif row['taxon'] == 'arabiensis':
        color='lightgreen'
    else: 
        color='gray'

    marker = Marker(location=(lat, long), draggable=False, opacity=0.7, color=color)
    m.add_layer(marker);

    message2 = HTML()
    message2.value = f"n = {row['count']}"
    marker.popup = message2

display(m)

Map(center=[9.28, -10.03], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_o…

In [16]:

if min_month >= 0:
    # For this cohort we have month data, so show a breakdown of sample
    # numbers by location and month.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.pivot_table(
        index=["location", "longitude", "latitude"],
        columns="month",
        values="sample_id",
        aggfunc="count",
        fill_value=0,
    )

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude")] + 
        [("Date", pd.to_datetime(x, format="%m").month_name()) 
         for x in df_loc_dt.columns[3:]], 
    )
    df_loc_dt.columns = cols
    
else:
    # For this cohort we do not have month data, so show a breakdown of sample
    # numbers by location only.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.groupby(["location", "longitude", "latitude"]).agg({"sample_id": "count"})

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude"), ("Date", cohort.year)]
    )
    df_loc_dt.columns = cols

# Style the table.
df_loc_dt_styled = (
    df_loc_dt
    .style
    .format(precision=3)
    .set_caption("Number of samples collected.")
    .hide()
)
display(df_loc_dt_styled)    

## Diagnostics
### H12 calibration

In [17]:
display(Markdown(f"Selected window size: **{h12_window_size:,}**"))

window_sizes = (100, 200, 500, 1000, 2000, 5000, 10000, 20000)

ag3.plot_h12_calibration(
    contig=h12_calibration_contig,
    analysis=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);


Selected window size: **1,000**

### G123 Calibration

In [18]:
display(Markdown(f"Selected window size: **{g123_window_size:,}**"))

ag3.plot_g123_calibration(
    contig=h12_calibration_contig,
    sites=phasing_analysis,
    site_mask=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);

Selected window size: **500**

## Data sources

In [19]:
df_sources_style = (
    df_contributors
    .style
    .set_caption("MalariaGEN Vector Observatory partners, studies and sample sets contributing data for this cohort.")
)
df_sources_style